In [1]:
from surprise import BaselineOnly
from surprise import Dataset
from surprise import Reader
from surprise.model_selection import cross_validate
                                                                                                                            
import pandas as pd
import numpy as np
import pymongo 
from pythainlp import sent_tokenize

client = pymongo.MongoClient("mongodb://aitulib.com:27017/")
db = client["turec_db"]

In [2]:
def create_rating_pd():
    data = list(db.sim_rate.find().limit(10000))
    ratings = pd.DataFrame(data)
    ratings = ratings.drop('_id', axis=1)
    return ratings

In [3]:
ratings = create_rating_pd()
ratings

borrowernumber biblionumber  rating
0              3222       161503     5.0
1              3222       619849     5.0
2              3222       690445     5.0
3              3222       679121     5.0
4            174597        53551     1.0
...             ...          ...     ...
4067         171411       378518     5.0
4068         171411       665284     5.0
4069         171411       522183     5.0
4070         171411       363720     5.0
4071         171411       697231     5.0

[4072 rows x 3 columns]

In [4]:
pd.options.display.max_colwidth = 200
pd.options.display.max_rows = 800


In [5]:
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer

In [6]:
r_limit = 50000
books = db.book_map3.find(no_cursor_timeout=True).sort([("rating_count", -1), ("rating_avg", -1)]).limit(r_limit)
content_df = pd.DataFrame(list(books))
content_df.drop('_id', axis=1, inplace=True)
content_df = content_df.set_index('biblionumber')
content_df

/usr/local/Cellar/jupyterlab/3.0.16_1/libexec/lib/python3.9/site-packages/pymongo/collection.py:1532: UserWarning: use an explicit session with no_cursor_timeout=True otherwise the cursor may still timeout after 30 minutes, for more info see https://docs.mongodb.com/v4.4/reference/method/cursor.noCursorTimeout/#session-idle-timeout-overrides-nocursortimeout
  return Cursor(self, *args, **kwargs)


title  \
biblionumber                                                                                                                                                           
600363                                                                                                               กฎหมายวิธีพิจารณาความอาญา. เล่ม 1 / คนึง ฦาไชย.   
714806                                                                                                                                              Things of techno   
608784                                                                                                               กฎหมายวิธีพิจารณาความอาญา. เล่ม 2 / คนึง ฦาไชย.   
696113                                                                   880-02 เซเปียนส์ : ประวัติย่อมนุษยชาติ / ยูวัล โนอาห์ แฮรารี เขียน ; นำชัย ชีววิวรรธน์ แปล.   
664720        880-02 การเมืองเปรียบเทียบ : ทฤษฎี แนวคิด และกรณีศึกษา = Comparative politics : theories, concepts & case studies / ไชยวัฒน์ ค้ำชู, นิธิ เนื่องจำนงค์.   
...                                                                                                                                                              ...   
624862                                                                                                 Case studies in allergic disorders / Hans Oettgen, Raif Geha.   
706373                                                           A manga lover's Tokyo travel guide : [my favorite things to see and do in Japan!] / Evangeline Neo.   
643072                                   Income contingent loans : theory, practice and prospects / edited by Bruce Chapman, Timothy Higgins and Joseph E. Stiglitz.   
643007                                                                                     The ethics of researching war : looking for Bosnia / Elizabeth Dauphinée.   
666265                                                                                     Probability and statistics for engineering and the sciences / Jay Devore.   

              rating_count  rating_avg  \
biblionumber                             
600363                  32        3.56   
714806                  29        3.32   
608784                  28        3.24   
696113                  23        2.84   
664720                  22        2.76   
...                    ...         ...   
624862                   0        1.00   
706373                   0        1.00   
643072                   0        1.00   
643007                   0        1.00   
666265                   0        1.00   

                                                                                                                                                                                               soup  \
biblionumber                                                                                                                                                                                          
600363                                                                                                                                                                 วิธีพิจารณาความอาญา. 181667    
714806                                                                                                                                                                                                
608784                                                                                                                                                                 วิธีพิจารณาความอาญา. 181667    
696113        880-04 อารยธรรม ประวัติ. 50617 880-05 มนุษย์ ประวัติ. 791109 880-06 ประวัติศาสตร์โลก. 34514 880-07 ลำดับเหตุการณ์ทางประวัติศาสตร์. 50416 880-08 เทคโนโลยีกับอารยธรรม ประวัติ. 791110    
664720                                                                                                                                                    880-05 การบริหารรัฐกิจเปรียบเทียบ. 42796    
...                               

In [7]:
def create_soup(x):
    temp = x['title'] + " " + x['soup']
    l = sent_tokenize(temp, engine="whitespace+newline")
    return " ".join(l)

In [8]:
content_df['soup_final'] = content_df.apply(create_soup, axis=1)
count_vector = CountVectorizer(stop_words='english')
count_matrix = count_vector.fit_transform(content_df[:r_limit]['soup_final'])

content_df.head(100)

title  \
biblionumber                                                                                                                                                                                                            
600363                                                                                                                                                                กฎหมายวิธีพิจารณาความอาญา. เล่ม 1 / คนึง ฦาไชย.   
714806                                                                                                                                                                                               Things of techno   
608784                                                                                                                                                                กฎหมายวิธีพิจารณาความอาญา. เล่ม 2 / คนึง ฦาไชย.   
696113                                                                                                                    880-02 เซเปียนส์ : ประวัติย่อมนุษยชาติ / ยูวัล โนอาห์ แฮรารี เขียน ; นำชัย ชีววิวรรธน์ แปล.   
664720                                                         880-02 การเมืองเปรียบเทียบ : ทฤษฎี แนวคิด และกรณีศึกษา = Comparative politics : theories, concepts & case studies / ไชยวัฒน์ ค้ำชู, นิธิ เนื่องจำนงค์.   
696854        880-02 คำอธิบายประมวลกฎหมายแพ่งและพาณิชย์ เรียงมาตรา ว่าด้วยจัดการงานนอกสั่ง ลาภมิควรได้ ละเมิด บรรพ 2 มาตรา 395-452 / จิตติ ติงศภัทิย์ ; ปรับปรุงโดย เขมภูมิ ภูมิถาวร, ชวิน อุ่นภัทร, อำนาจ ตั้งคีร...   
712437                                                                                                                                                                     880-02 หลักกฎหมายมรดก / ไพโรจน์ กัมพูสิริ.   
647540                                                                                                                                                                880-02 กฎหมายระหว่างประเทศ / จตุรนต์ ถิระวัฒน์.   
702492                                                                  880-02 บริหารธุรกิจ: ความสำเร็จและความยั่งยืนบนการสร้างคุณค่า = Business : creating value for success and sustainability / วิทยา ด่านธำรงกูล.   
672974                                                                               880-02 ความรู้เบื้องต้นเกี่ยวกับกฎหมายเศรษฐกิจระหว่างประเทศ = Introduction to international economc law / นาถนิรันดร์ จันทร์งาม.   
608512                                                                                                                                                              กฎหมายปกครองของประเทศในยุโรป / ปิยบุตร แสงกนกกุล.   
717023                                                                                                                                                                                    ปากกาสไตลัส (Momax OneLink)   
684038                                                                                                                                                  880-02 ความรู้เบื้องต้นเกี่ยวกับกฎหมายทั่วไป / หยุด แสงอุทัย.   
711434                                                                                                                                                       880-02 หลักพื้นฐานกฎหมายมหาชน / เกรียงไกร เจริญธนาวัฒน์.   
706127                                                                                                            880-02 คำอธิบายหลักพื้นฐานของกฎหมายเอกชน = Basic principle of private law / ศนันท์กรณ์ โสตถิพันธุ์.   
715188                                                                                                                                                    880-02 คำอธิบายกฎหมายอาญา ภาคทั่วไป / ทวีเกียรติ มีนะกนิษฐ.   
711437                     880-02 ระบบกฎหมายซีวิลลอว์ : จากกฎหมายสิบสองโต๊ะสู่ประมวลกฎหมายแพ่งและพาณิชย์ = [The civil law systems : from the Twelve Tables to the Thai civil and commercial code] / มุนินทร์ พงศาปาน.   
642406        880-02 คำอธิบายประมวลกฎหมายแพ่งและพาณิชย์ เรียงมาตรา ว่าด้วยจัดการงานนอ

In [9]:
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.metrics import mean_squared_error

In [10]:
content_cosine_sim = cosine_similarity(count_matrix, count_matrix)
content_cosine_sim.shape

(6235, 6235)

In [11]:
content_sim_df = pd.DataFrame(content_cosine_sim, index=content_df[:r_limit].index, columns=content_df[:r_limit].index)
content_sim_df

biblionumber  600363  714806  608784    696113    664720    696854    712437  \
biblionumber                                                                   
600363           1.0     0.0     1.0  0.000000  0.000000  0.000000  0.000000   
714806           0.0     1.0     0.0  0.000000  0.000000  0.000000  0.000000   
608784           1.0     0.0     1.0  0.000000  0.000000  0.000000  0.000000   
696113           0.0     0.0     0.0  1.000000  0.235702  0.331042  0.377964   
664720           0.0     0.0     0.0  0.235702  1.000000  0.195069  0.267261   
...              ...     ...     ...       ...       ...       ...       ...   
624862           0.0     0.0     0.0  0.000000  0.133333  0.000000  0.000000   
706373           0.0     0.1     0.0  0.000000  0.000000  0.000000  0.000000   
643072           0.0     0.0     0.0  0.000000  0.000000  0.000000  0.000000   
643007           0.0     0.0     0.0  0.000000  0.000000  0.000000  0.000000   
666265           0.0     0.0     0.0  0.000000  0.000000  0.000000  0.000000   

biblionumber    647540    702492    672974  ...    671823    689374  656738  \
biblionumber                                ...                               
600363        0.000000  0.000000  0.000000  ...  0.000000  0.000000     0.0   
714806        0.000000  0.000000  0.000000  ...  0.000000  0.000000     0.0   
608784        0.000000  0.000000  0.000000  ...  0.000000  0.000000     0.0   
696113        0.375000  0.393106  0.322329  ...  0.410152  0.243855     0.0   
664720        0.265165  0.221470  0.189934  ...  0.209460  0.123797     0.0   
...                ...       ...       ...  ...       ...       ...     ...   
624862        0.000000  0.000000  0.000000  ...  0.000000  0.000000     0.0   
706373        0.000000  0.000000  0.000000  ...  0.000000  0.000000     0.0   
643072        0.000000  0.000000  0.000000  ...  0.000000  0.000000     0.0   
643007        0.000000  0.000000  0.000000  ...  0.000000  0.000000     0.0   
666265        0.000000  0.000000  0.000000  ...  0.026812  0.000000     0.0   

biblionumber    609882    681890    624862  706373  643072  643007  666265  
biblionumber                                                                
600363        0.000000  0.000000  0.000000     0.0     0.0     0.0     0.0  
714806        0.000000  0.000000  0.000000     0.1     0.0     0.0     0.0  
608784        0.000000  0.000000  0.000000     0.0     0.0     0.0     0.0  
696113        0.000000  0.000000  0.000000     0.0     0.0     0.0     0.0  
664720        0.036370  0.000000  0.133333     0.0     0.0     0.0     0.0  
...                ...       ...       ...     ...     ...     ...     ...  
624862        0.130931  0.000000  1.000000     0.0     0.0     0.0     0.0  
706373        0.000000  0.000000  0.000000     1.0     0.0     0.0     0.0  
643072        0.000000  0.089722  0.000000     0.0     1.0     0.0     0.0  
643007        0.000000  0.000000  0.000000     0.0     0.0     1.0     0.0  
666265        0.000000  0.000000  0.000000     0.0     0.0     0.0     1.0  

[6235 rows x 6235 columns]

In [12]:
from joblib import dump, load

In [13]:
dump(content_sim_df, 'content_sim_df.joblib')

['content_sim_df.joblib']

In [14]:
dump(content_df, 'book_map.joblib')

['book_map.joblib']

In [15]:
indices = content_sim_df.loc["611661"].sort_values(ascending=False).index
content_df.loc[indices].head(100)

KeyError: '611661'

In [16]:
def sim_content(bib): 
    indices = content_sim_df.loc[bib].sort_values(ascending=False).index
    return content_df.loc[indices]

In [17]:
content_df[content_df['title'].str.match('.*king.*')  == True].head(20)

title  \
biblionumber                                                                                                                                                                                                            
707680          880-02 หลักพื้นฐานของกฎหมายการลงทุนระหว่างประเทศและการดำเนินการลงทุนระหว่างประเทศ = Fundamentals of international investment law and the making of international investments / นาถนิรันดร์ จันทร์งาม.   
696075                                                                                                              880-02 คู่มือออกแบบชีวิตด้วย Design thinking / Bill Burnett & Dave Evans ; เมษ์ ศรีพัฒนาสกุล แปล.   
714535                                                                                                880-02 ศิลปะแห่งการอ่านคน = Talking to strangers / มัลคอล์ม แกลดเวลล์ ผู้เขียน ; นุชนาฎ เนตรประเสริฐศรี ผู้แปล.   
716519        880-02 ประวัติศาสตร์สแกนดิเนเวีย : จากแดนอารยธรรมไวกิ้ง สู่ต้นแบบรัฐสวัสดิการโลกร่วมสมัย สังคมเสรีประชาธิปไตย และกำเนิดบลูทูธ! = History of Scandinavia : from the Viking age to welfare states, soc...   
689721                                                                                                                              880-02 ฮุกกะ : ปรัชญาความสุขฉบับเดนมาร์ก / โดย Meik Wiking ; พลอยแสง เอกญาติ แปล.   
708455                                                                   880-02 คู่มือการคิดเชิงออกแบบ = The design thinking playbook / Michael Lewrick, Patrick Link, Larry Leifer เขียน ; วิญญู กิ่งหิรัญวัฒนา แปล.   
713402                                                                                      880-02 ว่าด้วยความคิดทางการเมืองของฌาคส์ ร็องซีแยร์ = The political thinking of Jacques Ranciere / ไชยรัตน์ เจริญสินโอฬาร   
714673                                                                                                                                                   An introduction to service design thinking / Kom Campiranon.   
718202                                                                                                      Learning to think things through : a guide to critical thinking across the curriculum / Gerald M. Nosich.   
718203                                                                                                                                          The Pearson guide to critical and creative thinking / Robert DiYanni.   
716360                                                                                                                       Good vibes, good life : how self-love is the key to unlocking your greatness / Vex King.   
619958                                                                                                                Rethinking secularism / edited by Craig Calhoun, Mark Juergensmeyer, and Jonathan VanAntwerpen.   
713506                                                                                                                                       880-02 นกต่อ = The kingdom / Fuminori Nakamura ; กนกวรรณ เกตุชัยมาศ แปล.   
681218                                                                                                                                                              Critical thinking : the basics / Stuart Hanscomb.   
710984                                                 The decision maker's playbook : 12 mental tactics for thinking more clearly, navigating uncertainty and making smarter choices / Simon Mueller and Julia Dhar.   
605650                                                                                                         Policy-making in the European Union / edited by Helen Wallace, Mark A. Pollack, and Alasdair R. Young.   
701696                                                                                                                                                                                  Mockingjay / Suzanne Collins.   
679180                                                                               

In [18]:
h = sim_content("614438")
h.head(10)

KeyError: '614438'

In [19]:
ratings.head(100)

borrowernumber biblionumber  rating
0            3222       161503   5.000
1            3222       619849   5.000
2            3222       690445   5.000
3            3222       679121   5.000
4          174597        53551   1.000
5          174597        53551   1.000
6          174597       714237   1.000
7          174597       696847   1.400
8          174597       428647   1.400
9          174597       600981   1.400
10         174597       500778   1.400
11         174597       686110   1.000
12         174597       702105   1.000
13         174597       553555   1.000
14         174597       553555   1.000
15         174597       633034   1.000
16         175619       716848   2.568
17         148118       718724   2.536
18         158378       609086   1.000
19         158378       630103   1.000
20         158378       490217   1.000
21         152823       636577   1.400
22         152823       715181   1.400
23         152823       622834   1.400
24         152823       714471   1.400
25         152823       643077   3.000
26         152823       700075   3.000
27         148881       701157   2.600
28         148881       650255   3.704
29         148881       717521   2.200
30         148881       717522   2.200
31         148881       716546   3.736
32         162284       619184   5.000
33         162284       589674   5.000
34         162284       534202   5.000
35         162284       660412   5.000
36         162284       632582   5.000
37         162284       663461   5.000
38         162284       486064   5.000
39         162284       637496   5.000
40         162284       713343   5.000
41         148017       681182   1.400
42         177191       208128   1.000
43         173810       510153   1.000
44         173810       698296   1.400
45         173810       718470   1.400
46         173810       709824   1.400
47         173810       696244   1.400
48         173810       667232   2.968
49         173810       716972   1.400
50         173810       718783   2.936
51         173810       633264   2.744
52         173810       713781   1.400
53         173810       718785   3.336
54         173810       564853   1.800
55         173810       707806   2.600
56         160253       355392   5.000
57         160253       673487   5.000
58         160253       709917   5.000
59         160253       502656   5.000
60         174251       705488   2.536
61         173793       717095   1.000
62         173793       717096   1.000
63         173793       717097   1.000
64         173793       717600   1.000
65         173793       717020   1.000
66         173793       717021   1.000
67         173793       717447   1.800
68         173793       717446   1.800
69         173793       717448   1.800
70         179559       368958   1.000
71         179559       380895   1.000
72         158414       684100   1.000
73         158414       448523   1.000
74         158414       708935   1.000
75         158414       682289   1.400
76         158414       700479   2.200
77         158414       715453   2.200
78         158414       684263   2.200
79         158414       699603   1.800
80         158414       710833   1.800
81         158414       621207   2.584
82         145349       532179   1.000
83         145349       608784   1.704
84         145349       705913   3.080
85         145349       656416   1.800
86         145349       716855   2.200
87         145349       684957   2.600
88         145349       618095   3.000
89         145349       656895   5.000
90         145349       715187   5.000
91         145349       673326   5.000
92         145349       682806   2.408
93         174701        76319   1.000
94         174701       710808   1.000
95         151318       565461   5.000
96         151318       585247   5.000
97         151318       705218   2.200
98         151318       451087   5.000
99         151318       500021   2.200

In [20]:
from surprise import dump
_, knn_u_bl = dump.load('knn_u_bl')

In [21]:
list(knn_u_bl.trainset.all_ratings())

[(0, 0, 1.4),
 (0, 975, 5.0),
 (0, 1762, 1.7999999999999998),
 (0, 3100, 1.7999999999999998),
 (0, 4615, 1.7999999999999998),
 (0, 3936, 5.0),
 (0, 7352, 4.6),
 (0, 679, 2.952),
 (0, 8643, 1.4),
 (0, 7352, 4.6),
 (0, 11204, 4.776),
 (0, 10479, 1.4),
 (0, 12552, 1.7999999999999998),
 (0, 14473, 1.7999999999999998),
 (0, 6397, 5.0),
 (0, 16749, 5.0),
 (0, 16920, 5.0),
 (0, 17442, 1.7999999999999998),
 (0, 17891, 1.7999999999999998),
 (0, 4504, 3.8),
 (0, 17080, 4.2),
 (0, 26974, 1.4),
 (0, 5948, 5.0),
 (1, 1, 1.7999999999999998),
 (2, 2, 3.768),
 (2, 1877, 3.768),
 (2, 5618, 3.768),
 (2, 8285, 2.4079999999999995),
 (2, 20166, 3.7359999999999998),
 (2, 24921, 3.768),
 (2, 8285, 2.4079999999999995),
 (3, 3, 1.4),
 (3, 1011, 2.3759999999999994),
 (3, 3384, 1.4),
 (3, 3558, 2.776),
 (3, 4292, 2.5359999999999996),
 (3, 5255, 2.5039999999999996),
 (3, 5640, 1.0),
 (3, 6626, 1.0),
 (3, 6878, 1.4),
 (3, 7413, 1.8319999999999999),
 (3, 9457, 2.5679999999999996),
 (3, 9628, 2.872),
 (3, 10230, 2.5

In [22]:
iuid = knn_u_bl.trainset.to_inner_uid("68")
iuid

3429

In [23]:
kusers = knn_u_bl.get_neighbors(iuid, k=100)
ku_raw = (knn_u_bl.trainset.to_raw_uid(i) for i in kusers)
list(ku_raw)

['131500',
 '171232',
 '908',
 '142752',
 '109892',
 '160260',
 '133070',
 '98118',
 '133072',
 '122306',
 '167155',
 '144905',
 '111812',
 '100584',
 '156715',
 '151796',
 '140118',
 '100510',
 '136109',
 '90576',
 '60446',
 '134473',
 '118780',
 '139970',
 '133588',
 '159787',
 '1184',
 '133096',
 '116658',
 '138823',
 '139516',
 '138628',
 '117946',
 '167329',
 '65160',
 '145200',
 '164444',
 '70299',
 '1337',
 '149763',
 '131495',
 '85749',
 '113119',
 '132833',
 '162215',
 '139923',
 '145027',
 '73734',
 '141100',
 '112024',
 '116217',
 '98097',
 '151229',
 '7465',
 '117642',
 '139931',
 '145863',
 '144725',
 '1567',
 '158699',
 '34718',
 '113281',
 '73555',
 '1113',
 '144631',
 '73492',
 '144888',
 '150217',
 '160248',
 '139510',
 '3203',
 '139534',
 '112086',
 '159538',
 '150568',
 '387',
 '161221',
 '145674',
 '117637',
 '133080',
 '145829',
 '117998',
 '141720',
 '116006',
 '141989',
 '51977',
 '140461',
 '146331',
 '154564',
 '19398',
 '148505',
 '131918',
 '147515',
 '60704'